# Seminar "Computational Social Science" - Data Preparation

In [1]:
# import modules
import pandas as pd
import numpy as np
import requests
from bs4 import BeautifulSoup
import re
import os
import wptools
import gender_guesser.detector

# set working directory
wd = 'D:/IMDb Daten/'
os.chdir(wd)

# note: get data sets from https://www.imdb.com/interfaces/

### Some functions that will be needed later-on

In [2]:
# import data from tsv format (separated by \t) as pandas dataframe
def import_tsv(data_path):
    data_df = pd.read_csv(data_path, sep='\t')
    return data_df

def import_csv(data_path):
    data_df = pd.read_csv(data_path, sep=',')
    return data_df

# save data as csv (but with \t separator) to working directory (default) or path as given
def save_csv(df, filename, path=os.getcwd()):
    df.to_csv(path+filename+'.csv', sep='\t', index=False)

### Import and modify data set 'title.basics'
title.basics is structured as follows
- variable 'tconst' is a unique identifier for every title
- a title can be a movie, a television series (as a whole), a single television series episode,...
- for every title the basic information is given:
    - type of genre (movie, TV series, TV series episode,...)
    - genre (up to 3 genres per title)
    - year
    - ...

In [3]:
# import
df_title_basics = import_tsv(wd+'/title.basics.tsv/data.tsv')
len(df_title_basics.index)
# 6,682,995 titles

C:\Users\hanna\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3254: DtypeWarning: Columns (5) have mixed types.Specify dtype option on import or set low_memory=False.
  if (await self.run_code(code, result,  async_=asy)):


6682995

In [4]:
# keep only titles that are TV series episodes
df_title_basics = df_title_basics[df_title_basics.titleType == 'tvEpisode']
len(df_title_basics.index)
# 4,746,174 titles

4746174

In [5]:
# keep only titles where genre is (among other) drama:

# 1) split genre column into 3
genres = df_title_basics['genres'].str.split(',', n = 2, expand = True) 
df_title_basics['genre1']= genres[0]
df_title_basics['genre2']= genres[1]
df_title_basics['genre3']= genres[2]
del genres

# 2) create variable for whether title has genre drama
df_title_basics['isDrama'] = 0
df_title_basics['isDrama'] = np.where(df_title_basics.genre1=='Drama', 1,df_title_basics['isDrama'])
df_title_basics['isDrama'] = np.where(df_title_basics.genre2=='Drama', 1,df_title_basics['isDrama'])
df_title_basics['isDrama'] = np.where(df_title_basics.genre3=='Drama', 1,df_title_basics['isDrama'])

# 3) drop titles that are not of genre drama
df_title_basics = df_title_basics[df_title_basics.isDrama == 1]

In [6]:
# drop titles before 2000
df_title_basics = df_title_basics[df_title_basics.startYear != '\\N']
df_title_basics['startYear']= df_title_basics['startYear'].astype(int)
df_title_basics = df_title_basics[df_title_basics.startYear >= 2000]

len(df_title_basics.index)
# 359,943 titles

359943

In [7]:
# make list of titles (unique title identifier 'tconst') that are left
title_list = df_title_basics['tconst'].tolist()

### Import and modify data set 'title.principals'
title.principals:
- for every title the main/principal crew and cast involved (directors, producers, writers, main actors,...) is given
- for every one of these principals for each title there is a new row in the data set, i.e. there may be multiple rows for each title
- for each principal there is information on:
    - job category (e.g. director, actor, writer,...)
    - more detailed job description (e.g. writers can be creator, show runner, but also author of the book the series is based on...)
    - ...

In [8]:
# import
df_title_principals = import_tsv(wd+'/title.principals.tsv/data.tsv')

In [9]:
# drop titles from title_principals that are not in titles list

df_title_principals['isinTitles'] = df_title_principals['tconst'].isin(title_list)
df_title_principals = df_title_principals[df_title_principals.isinTitles == True]

In [10]:
# show job categories
df_title_principals.category.unique()

array(['composer', 'actor', 'actress', 'director', 'writer', 'producer',
       'cinematographer', 'editor', 'production_designer', 'self',
       'archive_footage', 'archive_sound'], dtype=object)

In [11]:
# keep only title entries with writers and producers, keep in separate dataframes

df_title_writers = df_title_principals[df_title_principals.category == 'writer']
df_title_producers = df_title_principals[df_title_principals.category == 'producer']
del df_title_principals

In [12]:
# exclude certain types of writers (such as novel by, etc.)

# 1) list of different writer categories
writer_categories = df_title_writers.job.unique()
writer_categories = list(writer_categories)

# 2) list of key words (stems) indicating that writer is not screenwriter
patterns = ['book',
            'novel',
            'based',
            'manga',
            'comic',
            'inspir',
            'original',
            'short stor',
            'libretto',
            'consultant',
            'fairy',
            'character',
            'arising']

# 3) iterate over writer categories and append to list if keyword matches
exclude = []
for i in range(len(writer_categories)):
    job = writer_categories[i]
    for j in range(len(patterns)):
        pattern = patterns[j]
        if re.match(pattern, job, re.IGNORECASE):
            exclude.append(job)
            break
        else:
            continue

# 3) drop if writer description is in 'exclude' list       
df_title_writers['exclude'] = df_title_writers['job'].isin(exclude)
df_title_writers = df_title_writers[df_title_writers.exclude == False]

In [13]:
# drop titles with no information on producer and/or writer

# 1) lists of titles with info on writers/producers
title_list_w = df_title_writers['tconst'].tolist()
title_list_p = df_title_producers['tconst'].tolist()

# 2) remove duplicates by making lists to sets
title_list_w = set(title_list_w)
title_list_p = set(title_list_p)

# 3) variable to indicate whether title has info on writer/producer
df_title_basics['hasWriter'] = df_title_basics['tconst'].isin(title_list_w)
df_title_basics['hasProducer'] = df_title_basics['tconst'].isin(title_list_p)

# 4) drop titles from df_titles_basics if no writer or producer
df_title_basics = df_title_basics[df_title_basics.hasWriter == True]
df_title_basics = df_title_basics[df_title_basics.hasProducer == True]

# 5) update list of titles
title_list = df_title_basics['tconst'].tolist()

In [14]:
# number of titles: 93,063
len(df_title_basics.index)

93063

### Import and merge information from data set 'title.episode' to 'title_basics'
title.episode:
- contains only titles that are TV episodes
- for every title information is given on:
    - the parent series, i.e. the identifier of the series as a whole
    - season number
    - episode number within the season

In [15]:
# import
df_title_episode = import_tsv(wd+'/title.episode.tsv/data.tsv')

In [16]:
# drop titles from title_episode that are not in df_title_basics / title_list

df_title_episode['isinTitles'] = df_title_episode['tconst'].isin(title_list)
df_title_episode = df_title_episode[df_title_episode.isinTitles == True]

In [17]:
# merge df_title_basics and df_title_episode to df_titles

df_titles=pd.merge(df_title_basics, df_title_episode, how ='inner', on ='tconst')
title_list = df_titles['tconst'].tolist()

del df_title_basics
del df_title_episode

len(title_list)
# 93,062

93062

In [18]:
# save current df_titles data set
save_csv(df_titles, 'df_titles1', path=wd)

In [20]:
# drop titles in df_title_writers and df_title_producers that are not in df_titles

df_title_writers['isinTitles'] = df_title_writers['tconst'].isin(title_list)
df_title_writers = df_title_writers[df_title_writers.isinTitles == True]

df_title_producers['isinTitles'] = df_title_producers['tconst'].isin(title_list)
df_title_producers = df_title_producers[df_title_producers.isinTitles == True]

### Get the location of the TV series (production country) and keep only US productions

In [21]:
# extract all parent series of episodes
parentSeries = list(set(df_titles['parentTconst'].tolist()))
len(parentSeries) # 5,902

5902

In [22]:
# new dataframe with country info on parent series
df_parentseries = pd.DataFrame(columns=['parentTconst', 'country'])

In [23]:
# get production country of parent series by scraping from IMDb page
# IMDb page can be accessed using the unique series identifier in the URL

counter=0
for i in range(len(parentSeries)):
    url="https://www.imdb.com/title/"+parentSeries[i]
    df_parentseries.loc[i,'parentTconst'] = parentSeries[i]
    r=requests.get(url)
    c=r.content
    soup = BeautifulSoup(c,features="lxml")
    samples = soup.find_all("div", attrs={"id":"titleDetails"})
    for tag in samples:
        divTags = tag.find_all("div", {"class": "txt-block"})
        for tag in divTags:
            if 'Country' in tag.text:
                country_info = tag.text
                country_info=re.sub(r'Country:\n','',country_info)
                country_info=re.sub(r'\n','',country_info)
                print(counter, country_info)
                df_parentseries.loc[i, 'country'] = country_info
                counter=counter+1
                break

0 South Korea
1 Japan
2 Japan
3 Germany|Austria
4 UK
5 UK
6 USA
7 France
8 Portugal
9 UK
10 Japan
11 UK|USA
12 Germany
13 USA
14 Finland
15 USA
16 UK
17 USA
18 UK|USA
19 Netherlands
20 Germany
21 Japan
22 Israel
23 USA
24 UK
25 Japan
26 UK|Australia|New Zealand|USA
27 Denmark
28 USA
29 UK
30 Portugal
31 Croatia
32 Brazil
33 Turkey
34 Germany
35 Italy
36 Australia
37 Argentina
38 USA
39 Canada|France
40 USA
41 Israel
42 Belgium
43 Mexico
44 Australia
45 USA
46 USA
47 Germany
48 Germany|France|Finland
49 India
50 Canada
51 Finland
52 South Africa
53 Colombia|Mexico
54 Poland
55 Canada
56 UK
57 Japan
58 France
59 USA|UK|Italy
60 Norway|Denmark
61 Hong Kong
62 Turkey
63 Sweden
64 Turkey
65 USA
66 Turkey
67 Norway
68 Germany
69 Taiwan
70 USA
71 USA
72 Canada
73 USA
74 Australia
75 Japan
76 USA
77 Germany
78 Argentina
79 Germany|Austria|Switzerland
80 Netherlands
81 Argentina
82 USA
83 Argentina
84 South Africa
85 Australia
86 UK
87 USA
88 France|Belgium|Switzerland|Czechoslovakia
89 UK
90 I

KeyboardInterrupt: 

In [ ]:
# save dataset
save_csv(df_parentseries, 'df_parentseries1')

In [24]:
# load dataset
#df_parentseries = import_tsv(wd+'df_parentseries1.csv')

In [25]:
# extract title IDs of parent series that have USA as location
location_usa = []

for i in df_parentseries.index:
    country = df_parentseries.loc[i, 'country']
    country=str(country)
    if 'USA' in country:
      location_usa.append(df_parentseries.loc[i, 'parentTconst'])

In [26]:
# save list with title IDs of (parent) series with location in USA as txt
with open(wd+'location_usa.txt', 'w') as filehandle:
 for title in location_usa:
     filehandle.write('%s\n' % title)

In [32]:
# drop series where location is not USA

# 1) drop from df_titles
df_titles['isinUSA'] = df_titles['parentTconst'].isin(location_usa)
df_titles = df_titles[df_titles.isinUSA == True]

# 2) update title_list
title_list = df_titles['tconst'].tolist()

# 3) drop titles from writers and producers df
df_title_writers['isinUSA'] = df_title_writers['tconst'].isin(title_list)
df_title_writers = df_title_writers[df_title_writers.isinUSA == True]

df_title_producers['isinUSA'] = df_title_producers['tconst'].isin(title_list)
df_title_producers = df_title_producers[df_title_producers.isinUSA == True]

In [37]:
# number of titles: 15,993
print(len(title_list))

# number of entries in df_title_writers: 39,190
print(len(df_title_writers.index))

# number of entries in df_title_producers: 23,117
print(len(df_title_producers.index))

15993
39190
23117


### Merge df_titles, df_title_writers and df_title_producers into one dataset

In [38]:
# how many writers/producers per title maximum?
print(df_title_writers['tconst'].value_counts())      # up to 9 writers per title
print(df_title_producers['tconst'].value_counts())    # up to 7 producers per title

tt10201504    9
tt1399918     7
tt0978291     7
tt0975612     6
tt0975586     6
             ..
tt1157049     1
tt6886420     1
tt1618500     1
tt5986796     1
tt5127760     1
Name: tconst, Length: 15993, dtype: int64
tt2369512    7
tt3663796    7
tt2369450    6
tt2369442    6
tt1836664    5
            ..
tt1340525    1
tt1039940    1
tt7720460    1
tt2558980    1
tt4981514    1
Name: tconst, Length: 15993, dtype: int64


In [39]:
# add writers to df_titles
# Code segment takes quite a while!

# 1) add empty column for writers
df_titles['writers'] = ''

# 2) iterate through df_title_writers and add writers (separated by comma) for each title to the writers column in df_titles
counter=0
for i in df_title_writers.index:
    temp_t = df_title_writers.loc[i,'tconst']
    temp_w = df_title_writers.loc[i,'nconst']
    df_titles.loc[df_titles['tconst'] == temp_t, 'writers'] = df_titles['writers'] + ',' + temp_w
    print(counter, flush=True)
    counter=counter+1
    
# 3. separate writers column into 9 (or rather 10 but first col will be empty due to comma as first character)
writers = df_titles["writers"].str.split(",", n = 10, expand = True)
df_titles['writer1'] = writers[1]  # col with index 0 is empty
df_titles['writer2'] = writers[2]
df_titles['writer3'] = writers[3]
df_titles['writer4'] = writers[4]
df_titles['writer5'] = writers[5]
df_titles['writer6'] = writers[6]
df_titles['writer7'] = writers[7]
df_titles['writer8'] = writers[8]
df_titles['writer9'] = writers[9]
del writers

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

1861
1862
1863
1864
1865
1866
1867
1868
1869
1870
1871
1872
1873
1874
1875
1876
1877
1878
1879
1880
1881
1882
1883
1884
1885
1886
1887
1888
1889
1890
1891
1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060


3500
3501
3502
3503
3504
3505
3506
3507
3508
3509
3510
3511
3512
3513
3514
3515
3516
3517
3518
3519
3520
3521
3522
3523
3524
3525
3526
3527
3528
3529
3530
3531
3532
3533
3534
3535
3536
3537
3538
3539
3540
3541
3542
3543
3544
3545
3546
3547
3548
3549
3550
3551
3552
3553
3554
3555
3556
3557
3558
3559
3560
3561
3562
3563
3564
3565
3566
3567
3568
3569
3570
3571
3572
3573
3574
3575
3576
3577
3578
3579
3580
3581
3582
3583
3584
3585
3586
3587
3588
3589
3590
3591
3592
3593
3594
3595
3596
3597
3598
3599
3600
3601
3602
3603
3604
3605
3606
3607
3608
3609
3610
3611
3612
3613
3614
3615
3616
3617
3618
3619
3620
3621
3622
3623
3624
3625
3626
3627
3628
3629
3630
3631
3632
3633
3634
3635
3636
3637
3638
3639
3640
3641
3642
3643
3644
3645
3646
3647
3648
3649
3650
3651
3652
3653
3654
3655
3656
3657
3658
3659
3660
3661
3662
3663
3664
3665
3666
3667
3668
3669
3670
3671
3672
3673
3674
3675
3676
3677
3678
3679
3680
3681
3682
3683
3684
3685
3686
3687
3688
3689
3690
3691
3692
3693
3694
3695
3696
3697
3698
3699


5139
5140
5141
5142
5143
5144
5145
5146
5147
5148
5149
5150
5151
5152
5153
5154
5155
5156
5157
5158
5159
5160
5161
5162
5163
5164
5165
5166
5167
5168
5169
5170
5171
5172
5173
5174
5175
5176
5177
5178
5179
5180
5181
5182
5183
5184
5185
5186
5187
5188
5189
5190
5191
5192
5193
5194
5195
5196
5197
5198
5199
5200
5201
5202
5203
5204
5205
5206
5207
5208
5209
5210
5211
5212
5213
5214
5215
5216
5217
5218
5219
5220
5221
5222
5223
5224
5225
5226
5227
5228
5229
5230
5231
5232
5233
5234
5235
5236
5237
5238
5239
5240
5241
5242
5243
5244
5245
5246
5247
5248
5249
5250
5251
5252
5253
5254
5255
5256
5257
5258
5259
5260
5261
5262
5263
5264
5265
5266
5267
5268
5269
5270
5271
5272
5273
5274
5275
5276
5277
5278
5279
5280
5281
5282
5283
5284
5285
5286
5287
5288
5289
5290
5291
5292
5293
5294
5295
5296
5297
5298
5299
5300
5301
5302
5303
5304
5305
5306
5307
5308
5309
5310
5311
5312
5313
5314
5315
5316
5317
5318
5319
5320
5321
5322
5323
5324
5325
5326
5327
5328
5329
5330
5331
5332
5333
5334
5335
5336
5337
5338


6778
6779
6780
6781
6782
6783
6784
6785
6786
6787
6788
6789
6790
6791
6792
6793
6794
6795
6796
6797
6798
6799
6800
6801
6802
6803
6804
6805
6806
6807
6808
6809
6810
6811
6812
6813
6814
6815
6816
6817
6818
6819
6820
6821
6822
6823
6824
6825
6826
6827
6828
6829
6830
6831
6832
6833
6834
6835
6836
6837
6838
6839
6840
6841
6842
6843
6844
6845
6846
6847
6848
6849
6850
6851
6852
6853
6854
6855
6856
6857
6858
6859
6860
6861
6862
6863
6864
6865
6866
6867
6868
6869
6870
6871
6872
6873
6874
6875
6876
6877
6878
6879
6880
6881
6882
6883
6884
6885
6886
6887
6888
6889
6890
6891
6892
6893
6894
6895
6896
6897
6898
6899
6900
6901
6902
6903
6904
6905
6906
6907
6908
6909
6910
6911
6912
6913
6914
6915
6916
6917
6918
6919
6920
6921
6922
6923
6924
6925
6926
6927
6928
6929
6930
6931
6932
6933
6934
6935
6936
6937
6938
6939
6940
6941
6942
6943
6944
6945
6946
6947
6948
6949
6950
6951
6952
6953
6954
6955
6956
6957
6958
6959
6960
6961
6962
6963
6964
6965
6966
6967
6968
6969
6970
6971
6972
6973
6974
6975
6976
6977


...

33269
33270
33271
33272
33273
33274
33275
33276
33277
33278
33279
33280
33281
33282
33283
33284
33285
33286
33287
33288
33289
33290
33291
33292
33293
33294
33295
33296
33297
33298
33299
33300
33301
33302
33303
33304
33305
33306
33307
33308
33309
33310
33311
33312
33313
33314
33315
33316
33317
33318
33319
33320
33321
33322
33323
33324
33325
33326
33327
33328
33329
33330
33331
33332
33333
33334
33335
33336
33337
33338
33339
33340
33341
33342
33343
33344
33345
33346
33347
33348
33349
33350
33351
33352
33353
33354
33355
33356
33357
33358
33359
33360
33361
33362
33363
33364
33365
33366
33367
33368
33369
33370
33371
33372
33373
33374
33375
33376
33377
33378
33379
33380
33381
33382
33383
33384
33385
33386
33387
33388
33389
33390
33391
33392
33393
33394
33395
33396
33397
33398
33399
33400
33401
33402
33403
33404
33405
33406
33407
33408
33409
33410
33411
33412
33413
33414
33415
33416
33417
33418
33419
33420
33421
33422
33423
33424
33425
33426
33427
33428
33429
33430
33431
33432
33433
33434
3343

34635
34636
34637
34638
34639
34640
34641
34642
34643
34644
34645
34646
34647
34648
34649
34650
34651
34652
34653
34654
34655
34656
34657
34658
34659
34660
34661
34662
34663
34664
34665
34666
34667
34668
34669
34670
34671
34672
34673
34674
34675
34676
34677
34678
34679
34680
34681
34682
34683
34684
34685
34686
34687
34688
34689
34690
34691
34692
34693
34694
34695
34696
34697
34698
34699
34700
34701
34702
34703
34704
34705
34706
34707
34708
34709
34710
34711
34712
34713
34714
34715
34716
34717
34718
34719
34720
34721
34722
34723
34724
34725
34726
34727
34728
34729
34730
34731
34732
34733
34734
34735
34736
34737
34738
34739
34740
34741
34742
34743
34744
34745
34746
34747
34748
34749
34750
34751
34752
34753
34754
34755
34756
34757
34758
34759
34760
34761
34762
34763
34764
34765
34766
34767
34768
34769
34770
34771
34772
34773
34774
34775
34776
34777
34778
34779
34780
34781
34782
34783
34784
34785
34786
34787
34788
34789
34790
34791
34792
34793
34794
34795
34796
34797
34798
34799
34800
3480

36001
36002
36003
36004
36005
36006
36007
36008
36009
36010
36011
36012
36013
36014
36015
36016
36017
36018
36019
36020
36021
36022
36023
36024
36025
36026
36027
36028
36029
36030
36031
36032
36033
36034
36035
36036
36037
36038
36039
36040
36041
36042
36043
36044
36045
36046
36047
36048
36049
36050
36051
36052
36053
36054
36055
36056
36057
36058
36059
36060
36061
36062
36063
36064
36065
36066
36067
36068
36069
36070
36071
36072
36073
36074
36075
36076
36077
36078
36079
36080
36081
36082
36083
36084
36085
36086
36087
36088
36089
36090
36091
36092
36093
36094
36095
36096
36097
36098
36099
36100
36101
36102
36103
36104
36105
36106
36107
36108
36109
36110
36111
36112
36113
36114
36115
36116
36117
36118
36119
36120
36121
36122
36123
36124
36125
36126
36127
36128
36129
36130
36131
36132
36133
36134
36135
36136
36137
36138
36139
36140
36141
36142
36143
36144
36145
36146
36147
36148
36149
36150
36151
36152
36153
36154
36155
36156
36157
36158
36159
36160
36161
36162
36163
36164
36165
36166
3616

37367
37368
37369
37370
37371
37372
37373
37374
37375
37376
37377
37378
37379
37380
37381
37382
37383
37384
37385
37386
37387
37388
37389
37390
37391
37392
37393
37394
37395
37396
37397
37398
37399
37400
37401
37402
37403
37404
37405
37406
37407
37408
37409
37410
37411
37412
37413
37414
37415
37416
37417
37418
37419
37420
37421
37422
37423
37424
37425
37426
37427
37428
37429
37430
37431
37432
37433
37434
37435
37436
37437
37438
37439
37440
37441
37442
37443
37444
37445
37446
37447
37448
37449
37450
37451
37452
37453
37454
37455
37456
37457
37458
37459
37460
37461
37462
37463
37464
37465
37466
37467
37468
37469
37470
37471
37472
37473
37474
37475
37476
37477
37478
37479
37480
37481
37482
37483
37484
37485
37486
37487
37488
37489
37490
37491
37492
37493
37494
37495
37496
37497
37498
37499
37500
37501
37502
37503
37504
37505
37506
37507
37508
37509
37510
37511
37512
37513
37514
37515
37516
37517
37518
37519
37520
37521
37522
37523
37524
37525
37526
37527
37528
37529
37530
37531
37532
3753

38733
38734
38735
38736
38737
38738
38739
38740
38741
38742
38743
38744
38745
38746
38747
38748
38749
38750
38751
38752
38753
38754
38755
38756
38757
38758
38759
38760
38761
38762
38763
38764
38765
38766
38767
38768
38769
38770
38771
38772
38773
38774
38775
38776
38777
38778
38779
38780
38781
38782
38783
38784
38785
38786
38787
38788
38789
38790
38791
38792
38793
38794
38795
38796
38797
38798
38799
38800
38801
38802
38803
38804
38805
38806
38807
38808
38809
38810
38811
38812
38813
38814
38815
38816
38817
38818
38819
38820
38821
38822
38823
38824
38825
38826
38827
38828
38829
38830
38831
38832
38833
38834
38835
38836
38837
38838
38839
38840
38841
38842
38843
38844
38845
38846
38847
38848
38849
38850
38851
38852
38853
38854
38855
38856
38857
38858
38859
38860
38861
38862
38863
38864
38865
38866
38867
38868
38869
38870
38871
38872
38873
38874
38875
38876
38877
38878
38879
38880
38881
38882
38883
38884
38885
38886
38887
38888
38889
38890
38891
38892
38893
38894
38895
38896
38897
38898
3889

In [40]:
# save current dataset
save_csv(df_titles, 'df_titles2', path=wd)

In [41]:
# add producers to df_titles (analogous to adding writers (see above))

df_titles['producers'] = ''

total_entries = len(df_title_producers.index)
counter=0   
for i in df_title_producers.index:
    temp_t = df_title_producers.loc[i,'tconst']
    temp_p = df_title_producers.loc[i,'nconst']
    df_titles.loc[df_titles['tconst'] == temp_t, 'producers'] = df_titles['producers'] + ',' + temp_p
    counter=counter+1
    print(counter/total_entries, flush=True)
    
 
producers = df_titles['producers'].str.split(",", n = 8, expand = True)
df_titles['producer1'] = producers[1]
df_titles['producer2'] = producers[2]
df_titles['producer3'] = producers[3]
df_titles['producer4'] = producers[4]
df_titles['producer5'] = producers[5]
df_titles['producer6'] = producers[6]
df_titles['producer7'] = producers[7]

del producers


4.325820824501449e-05
8.651641649002898e-05
0.00012977462473504346
0.00017303283298005797
0.00021629104122507245
0.0002595492494700869
0.00030280745771510143
0.00034606566596011594
0.00038932387420513044
0.0004325820824501449
0.0004758402906951594
0.0005190984989401739
0.0005623567071851884
0.0006056149154302029
0.0006488731236752174
0.0006921313319202319
0.0007353895401652463
0.0007786477484102609
0.0008219059566552753
0.0008651641649002898
0.0009084223731453044
0.0009516805813903188
0.0009949387896353334
0.0010381969978803477
0.0010814552061253623
0.0011247134143703768
0.0011679716226153912
0.0012112298308604057
0.0012544880391054203
0.0012977462473504349
0.0013410044555954492
0.0013842626638404638
0.0014275208720854783
0.0014707790803304927
0.0015140372885755072
0.0015572954968205218
0.0016005537050655361
0.0016438119133105507
0.0016870701215555652
0.0017303283298005796
0.0017735865380455941
0.0018168447462906087
0.001860102954535623
0.0019033611627806376
0.0019466193710256522
0.001

0.01687070121555565
0.016913959423800667
0.01695721763204568
0.017000475840290696
0.017043734048535708
0.017086992256780724
0.01713025046502574
0.017173508673270752
0.017216766881515768
0.01726002508976078
0.017303283298005796
0.017346541506250812
0.017389799714495825
0.01743305792274084
0.017476316130985856
0.01751957433923087
0.017562832547475885
0.017606090755720897
0.017649348963965913
0.01769260717221093
0.01773586538045594
0.017779123588700957
0.01782238179694597
0.017865640005190985
0.017908898213436
0.017952156421681013
0.01799541462992603
0.01803867283817104
0.018081931046416058
0.018125189254661073
0.018168447462906086
0.0182117056711511
0.018254963879396114
0.01829822208764113
0.018341480295886146
0.018384738504131158
0.018427996712376174
0.018471254920621186
0.018514513128866202
0.018557771337111218
0.01860102954535623
0.018644287753601246
0.01868754596184626
0.018730804170091275
0.01877406237833629
0.018817320586581303
0.01886057879482632
0.01890383700307133
0.018947095211

0.03417398451356145
0.034217242721806464
0.03426050093005148
0.03430375913829649
0.034347017346541504
0.03439027555478652
0.034433533763031536
0.03447679197127655
0.03452005017952156
0.03456330838776658
0.03460656659601159
0.03464982480425661
0.034693083012501624
0.03473634122074663
0.03477959942899165
0.034822857637236665
0.03486611584548168
0.0349093740537267
0.03495263226197171
0.03499589047021672
0.03503914867846174
0.03508240688670675
0.03512566509495177
0.035168923303196785
0.035212181511441794
0.03525543971968681
0.035298697927931826
0.03534195613617684
0.03538521434442186
0.035428472552666866
0.03547173076091188
0.0355149889691569
0.035558247177401914
0.03560150538564693
0.03564476359389194
0.035688021802136954
0.03573128001038197
0.035774538218626986
0.035817796426872
0.03586105463511701
0.03590431284336203
0.03594757105160704
0.03599082925985206
0.036034087468097074
0.03607734567634208
0.0361206038845871
0.036163862092832115
0.03620712030107713
0.03625037850932215
0.036293636

0.05173681706103733
0.05178007526928235
0.051823333477527364
0.05186659168577237
0.05190984989401739
0.051953108102262405
0.05199636631050742
0.052039624518752436
0.052082882726997445
0.05212614093524246
0.05216939914348748
0.05221265735173249
0.05225591555997751
0.05229917376822252
0.052342431976467534
0.05238569018471255
0.052428948392957565
0.05247220660120258
0.05251546480944759
0.052558723017692606
0.05260198122593762
0.05264523943418264
0.052688497642427654
0.05273175585067266
0.05277501405891768
0.052818272267162694
0.05286153047540771
0.052904788683652726
0.052948046891897735
0.05299130510014275
0.05303456330838777
0.05307782151663278
0.0531210797248778
0.05316433793312281
0.05320759614136782
0.05325085434961284
0.053294112557857855
0.05333737076610287
0.05338062897434788
0.053423887182592895
0.05346714539083791
0.05351040359908293
0.05355366180732794
0.05359692001557295
0.05364017822381797
0.053683436432062984
0.053726694640308
0.053769952848553015
0.053813211056798024
0.05385

0.06942942423324826
0.06947268244149327
0.06951594064973829
0.0695591988579833
0.06960245706622832
0.06964571527447333
0.06968897348271835
0.06973223169096336
0.06977548989920837
0.0698187481074534
0.0698620063156984
0.06990526452394343
0.06994852273218843
0.06999178094043344
0.07003503914867847
0.07007829735692347
0.0701215555651685
0.0701648137734135
0.07020807198165852
0.07025133018990354
0.07029458839814855
0.07033784660639357
0.07038110481463858
0.07042436302288359
0.07046762123112861
0.07051087943937362
0.07055413764761864
0.07059739585586365
0.07064065406410866
0.07068391227235368
0.07072717048059869
0.07077042868884371
0.07081368689708872
0.07085694510533373
0.07090020331357876
0.07094346152182376
0.07098671973006879
0.0710299779383138
0.0710732361465588
0.07111649435480383
0.07115975256304884
0.07120301077129386
0.07124626897953887
0.07128952718778388
0.0713327853960289
0.07137604360427391
0.07141930181251893
0.07146256002076394
0.07150581822900895
0.07154907643725397
0.071592

...

0.9189773759570878
0.9190206341653329
0.9190638923735779
0.9191071505818229
0.9191504087900679
0.919193666998313
0.919236925206558
0.919280183414803
0.919323441623048
0.9193666998312929
0.919409958039538
0.919453216247783
0.919496474456028
0.919539732664273
0.919582990872518
0.9196262490807631
0.9196695072890081
0.9197127654972531
0.9197560237054981
0.9197992819137432
0.9198425401219882
0.9198857983302332
0.9199290565384782
0.9199723147467231
0.9200155729549682
0.9200588311632132
0.9201020893714582
0.9201453475797032
0.9201886057879483
0.9202318639961933
0.9202751222044383
0.9203183804126833
0.9203616386209283
0.9204048968291734
0.9204481550374184
0.9204914132456634
0.9205346714539083
0.9205779296621533
0.9206211878703984
0.9206644460786434
0.9207077042868884
0.9207509624951334
0.9207942207033785
0.9208374789116235
0.9208807371198685
0.9209239953281135
0.9209672535363586
0.9210105117446036
0.9210537699528486
0.9210970281610936
0.9211402863693385
0.9211835445775836
0.9212268027858286
0.

0.9377946965436692
0.9378379547519142
0.9378812129601591
0.9379244711684042
0.9379677293766492
0.9380109875848942
0.9380542457931392
0.9380975040013843
0.9381407622096293
0.9381840204178743
0.9382272786261193
0.9382705368343643
0.9383137950426094
0.9383570532508544
0.9384003114590994
0.9384435696673443
0.9384868278755893
0.9385300860838344
0.9385733442920794
0.9386166025003244
0.9386598607085694
0.9387031189168145
0.9387463771250595
0.9387896353333045
0.9388328935415495
0.9388761517497946
0.9389194099580396
0.9389626681662846
0.9390059263745296
0.9390491845827745
0.9390924427910196
0.9391357009992646
0.9391789592075096
0.9392222174157546
0.9392654756239996
0.9393087338322447
0.9393519920404897
0.9393952502487347
0.9394385084569797
0.9394817666652248
0.9395250248734698
0.9395682830817148
0.9396115412899597
0.9396547994982047
0.9396980577064498
0.9397413159146948
0.9397845741229398
0.9398278323311848
0.9398710905394299
0.9399143487476749
0.9399576069559199
0.9400008651641649
0.9400441233

0.9566120171302505
0.9566552753384955
0.9566985335467405
0.9567417917549855
0.9567850499632305
0.9568283081714756
0.9568715663797206
0.9569148245879656
0.9569580827962105
0.9570013410044556
0.9570445992127006
0.9570878574209456
0.9571311156291906
0.9571743738374356
0.9572176320456807
0.9572608902539257
0.9573041484621707
0.9573474066704157
0.9573906648786608
0.9574339230869058
0.9574771812951508
0.9575204395033957
0.9575636977116407
0.9576069559198858
0.9576502141281308
0.9576934723363758
0.9577367305446208
0.9577799887528659
0.9578232469611109
0.9578665051693559
0.9579097633776009
0.9579530215858459
0.957996279794091
0.958039538002336
0.958082796210581
0.9581260544188259
0.958169312627071
0.958212570835316
0.958255829043561
0.958299087251806
0.958342345460051
0.9583856036682961
0.9584288618765411
0.9584721200847861
0.9585153782930311
0.9585586365012762
0.9586018947095212
0.9586451529177662
0.9586884111260111
0.9587316693342561
0.9587749275425012
0.9588181857507462
0.9588614439589912
0

0.9753860795085868
0.9754293377168318
0.9754725959250767
0.9755158541333218
0.9755591123415668
0.9756023705498118
0.9756456287580568
0.9756888869663018
0.9757321451745469
0.9757754033827919
0.9758186615910369
0.9758619197992819
0.975905178007527
0.975948436215772
0.975991694424017
0.9760349526322619
0.9760782108405069
0.976121469048752
0.976164727256997
0.976207985465242
0.976251243673487
0.9762945018817321
0.9763377600899771
0.9763810182982221
0.9764242765064671
0.9764675347147121
0.9765107929229572
0.9765540511312022
0.9765973093394471
0.9766405675476921
0.9766838257559372
0.9767270839641822
0.9767703421724272
0.9768136003806722
0.9768568585889172
0.9769001167971623
0.9769433750054073
0.9769866332136523
0.9770298914218973
0.9770731496301424
0.9771164078383874
0.9771596660466324
0.9772029242548773
0.9772461824631223
0.9772894406713674
0.9773326988796124
0.9773759570878574
0.9774192152961024
0.9774624735043475
0.9775057317125925
0.9775489899208375
0.9775922481290825
0.9776355063373275


0.994203400095168
0.9942466583034131
0.9942899165116581
0.9943331747199031
0.9943764329281481
0.9944196911363932
0.9944629493446382
0.9945062075528832
0.9945494657611281
0.9945927239693731
0.9946359821776182
0.9946792403858632
0.9947224985941082
0.9947657568023532
0.9948090150105983
0.9948522732188433
0.9948955314270883
0.9949387896353333
0.9949820478435784
0.9950253060518234
0.9950685642600684
0.9951118224683133
0.9951550806765583
0.9951983388848034
0.9952415970930484
0.9952848553012934
0.9953281135095384
0.9953713717177834
0.9954146299260285
0.9954578881342735
0.9955011463425185
0.9955444045507635
0.9955876627590086
0.9956309209672536
0.9956741791754985
0.9957174373837435
0.9957606955919885
0.9958039538002336
0.9958472120084786
0.9958904702167236
0.9959337284249686
0.9959769866332137
0.9960202448414587
0.9960635030497037
0.9961067612579487
0.9961500194661937
0.9961932776744388
0.9962365358826838
0.9962797940909287
0.9963230522991737
0.9963663105074188
0.9964095687156638
0.99645282692

In [81]:
# save current dataset
save_csv(df_titles, 'df_titles3',path=wd)

In [ ]:
#df_titles = import_tsv(wd+'df_titles3.csv')

### New dataframe df_writers_producers
- each row is a pair of writer and producer who have worked together
- for every pair the number of collaborations is given

In [74]:
# create empty dataframe
df_writers_producers = pd.DataFrame(columns=['writer', 'producer', 'tconst', 'parentTconst', 
                                             'seasonNumber', 'episodeNumber'])

In [75]:
# functions for next step

def fill_df_row(df, row_counter, w, p, t, pt, sn, en):
    
    """
    Fills in one row of the writer_producer dataframe:
    one writer (w) and producer (p) pair, 
    unique title identifier (t),
    unique title identifier of parent series (pt),
    season number of title (sn),
    episode number of title in season (en)
    """
    
    df.loc[row_counter, 'writer'] = w
    df.loc[row_counter, 'producer'] = p
    df.loc[row_counter, 'tconst'] = t
    df.loc[row_counter, 'parentTconst'] = pt
    df.loc[row_counter, 'seasonNumber'] = sn
    df.loc[row_counter, 'episodeNumber'] = en
    
    return df

def fill_df_one_writer(df, row_counter, w, p, t, pt, sn, en,
                      temp_p2,temp_p3,temp_p4,temp_p5,temp_p6,temp_p7,
                      p2, p3, p4, p5, p6, p7):
    """
    Fills in all collaborations for one writer in one row
    """
    
    df = fill_df_row(df, row_counter, w, p, t, pt, sn, en)
    row_counter = row_counter+1
    if p2 == True:
        p=temp_p2
        df= fill_df_row(df, row_counter, w, p, t, pt, sn, en)
        row_counter = row_counter+1
        if p3 == True:
            p=temp_p3
            df= fill_df_row(df, row_counter, w, p, t, pt, sn, en)
            row_counter = row_counter+1
            if p4 == True:
                p=temp_p4
                df= fill_df_row(df, row_counter, w, p, t, pt, sn, en)
                row_counter = row_counter+1
                if p5 == True:
                    p=temp_p5
                    df= fill_df_row(df, row_counter, w, p, t, pt, sn, en)
                    row_counter = row_counter+1
                    if p6 == True:
                        p=temp_p6
                        df= fill_df_row(df, row_counter, w, p, t, pt, sn, en)
                        row_counter = row_counter+1
                        if p7 == True:
                            p=temp_p7
                            df= fill_df_row(df, row_counter, w, p, t, pt, sn, en)
                            row_counter = row_counter+1
    return df, row_counter


In [76]:
# iterate over titles and for each title put writers and producers pairwise in df_writers_producers

# number of titles: 15,993
row_counter = 0
iteration = 0

for i in df_titles.index:
    print(iteration, flush=True)
    iteration=iteration+1
    
    w2=w3=w4=w5=w6=w7=w8=w9=False
    p2=p3=p4=p5=p6=p7=False
    temp_w2=temp_w3=temp_w4=temp_w5=temp_w6=temp_w7=temp_w8=temp_w9=''
    temp_p2=temp_p3=temp_p4=temp_p5=temp_p6=temp_p7=''
    
    temp_w1 = df_titles.loc[i, 'writer1']
    temp_p1 = df_titles.loc[i, 'producer1']
    t = df_titles.loc[i, 'tconst']
    pt = df_titles.loc[i, 'parentTconst']
    sn = df_titles.loc[i, 'seasonNumber']
    en = df_titles.loc[i, 'episodeNumber']  
    
    # check for each row if there is writers 2-9 and producers 2-7
    # and store them in temp_ variables
    
    writers = [w2,w3,w4,w5,w6,w7,w8,w9]
    writers_temps = [temp_w2, temp_w3, temp_w4,temp_w5,temp_w6,temp_w7,temp_w8,temp_w9]
    writers_var_names = ['writer2','writer3','writer4','writer5','writer6','writer6','writer8','writer9']
    producers=[p2,p3,p4,p5,p6,p7]
    producers_temps = [temp_p2, temp_p3, temp_p4, temp_p5,temp_p6,temp_p7]
    producers_var_names = ['producer2','producer3','producer4','producer5','producer6','producer7']
    
    # fill in writer variables (w2, w3,... temp_w2, temp_w3,...)
    for j in range(len(writers)):
        var_name = writers_var_names[j]
        if not pd.isna(df_titles.loc[i, var_name]):
            writers[j] = True
            writers_temps[j] = df_titles.loc[i, var_name]
        else:
            break   
    w2,w3,w4,w5,w6,w7,w8,w9 = [writers[k] for k in range(len(writers))]
    temp_w2,temp_w3,temp_w4,temp_w5,temp_w6,temp_w7,temp_w8,temp_w9 = [writers_temps[k] for k in range(len(writers_temps))]
    
    # fill in producer variables (p2, p3,... temp_p2, temp_p3,...)
    for j in range(len(producers)):
        var_name = producers_var_names[j]
        if not pd.isna(df_titles.loc[i, var_name]):
            producers[j] = True
            producers_temps[j] = df_titles.loc[i, var_name]
        else:
            break
    p2,p3,p4,p5,p6,p7 = [producers[k] for k in range(len(producers))]
    temp_p2, temp_p3, temp_p4, temp_p5,temp_p6,temp_p7 = [producers_temps[k] for k in range(len(producers_temps))]
    
    # fill in first writer of row
    w = temp_w1
    p = temp_p1
    df_writers_producers, row_counter = fill_df_one_writer(df_writers_producers, row_counter, w, p, t, pt, sn, en,
                                                           temp_p2,temp_p3,temp_p4,temp_p5,temp_p6,temp_p7,
                                                           p2, p3, p4, p5, p6, p7)
    
    # fill in 2nd writer (if available)
    if w2 == True:
        w = temp_w2
        p = temp_p1
        df_writers_producers, row_counter = fill_df_one_writer(df_writers_producers, row_counter, w, p, t, pt, sn, en,
                                                           temp_p2,temp_p3,temp_p4,temp_p5,temp_p6,temp_p7,
                                                           p2, p3, p4, p5, p6, p7)
    else:
        continue
        
    # fill in 3rd writer    
    if w3 == True:
        w = temp_w3
        p = temp_p1
        df_writers_producers, row_counter = fill_df_one_writer(df_writers_producers, row_counter, w, p, t, pt, sn, en,
                                                           temp_p2,temp_p3,temp_p4,temp_p5,temp_p6,temp_p7,
                                                           p2, p3, p4, p5, p6, p7)
    else:
        continue
        
    # 4th writer ... 
    if w4 == True:
        w = temp_w4
        p = temp_p1
        df_writers_producers, row_counter = fill_df_one_writer(df_writers_producers, row_counter, w, p, t, pt, sn, en,
                                                           temp_p2,temp_p3,temp_p4,temp_p5,temp_p6,temp_p7,
                                                           p2, p3, p4, p5, p6, p7)
    else:
        continue
        
    # 5th writer ...   
    if w5 == True:
        w = temp_w5
        p = temp_p1
        df_writers_producers, row_counter = fill_df_one_writer(df_writers_producers, row_counter, w, p, t, pt, sn, en,
                                                           temp_p2,temp_p3,temp_p4,temp_p5,temp_p6,temp_p7,
                                                           p2, p3, p4, p5, p6, p7)
    else:
        continue
        
    # 6th writer ...
    if w6 == True:
        w = temp_w6
        p = temp_p1
        df_writers_producers, row_counter = fill_df_one_writer(df_writers_producers, row_counter, w, p, t, pt, sn, en,
                                                           temp_p2,temp_p3,temp_p4,temp_p5,temp_p6,temp_p7,
                                                           p2, p3, p4, p5, p6, p7)
    else:
        continue
        
    # 7th writer ...
    if w7 == True:
        w = temp_w7
        p = temp_p1
        df_writers_producers, row_counter = fill_df_one_writer(df_writers_producers, row_counter, w, p, t, pt, sn, en,
                                                           temp_p2,temp_p3,temp_p4,temp_p5,temp_p6,temp_p7,
                                                           p2, p3, p4, p5, p6, p7)
    else:
        continue
        
    # 8th writer ...
    if w8 == True:
        w = temp_w8
        p = temp_p1
        df_writers_producers, row_counter = fill_df_one_writer(df_writers_producers, row_counter, w, p, t, pt, sn, en,
                                                           temp_p2,temp_p3,temp_p4,temp_p5,temp_p6,temp_p7,
                                                           p2, p3, p4, p5, p6, p7)
    else:
        continue
        
    # 9th writer ...
    if w9 == True:
        w = temp_w9
        p = temp_p1
        df_writers_producers, row_counter = fill_df_one_writer(df_writers_producers, row_counter, w, p, t, pt, sn, en,
                                                           temp_p2,temp_p3,temp_p4,temp_p5,temp_p6,temp_p7,
                                                           p2, p3, p4, p5, p6, p7)


0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

1861
1862
1863
1864
1865
1866
1867
1868
1869
1870
1871
1872
1873
1874
1875
1876
1877
1878
1879
1880
1881
1882
1883
1884
1885
1886
1887
1888
1889
1890
1891
1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060


3500
3501
3502
3503
3504
3505
3506
3507
3508
3509
3510
3511
3512
3513
3514
3515
3516
3517
3518
3519
3520
3521
3522
3523
3524
3525
3526
3527
3528
3529
3530
3531
3532
3533
3534
3535
3536
3537
3538
3539
3540
3541
3542
3543
3544
3545
3546
3547
3548
3549
3550
3551
3552
3553
3554
3555
3556
3557
3558
3559
3560
3561
3562
3563
3564
3565
3566
3567
3568
3569
3570
3571
3572
3573
3574
3575
3576
3577
3578
3579
3580
3581
3582
3583
3584
3585
3586
3587
3588
3589
3590
3591
3592
3593
3594
3595
3596
3597
3598
3599
3600
3601
3602
3603
3604
3605
3606
3607
3608
3609
3610
3611
3612
3613
3614
3615
3616
3617
3618
3619
3620
3621
3622
3623
3624
3625
3626
3627
3628
3629
3630
3631
3632
3633
3634
3635
3636
3637
3638
3639
3640
3641
3642
3643
3644
3645
3646
3647
3648
3649
3650
3651
3652
3653
3654
3655
3656
3657
3658
3659
3660
3661
3662
3663
3664
3665
3666
3667
3668
3669
3670
3671
3672
3673
3674
3675
3676
3677
3678
3679
3680
3681
3682
3683
3684
3685
3686
3687
3688
3689
3690
3691
3692
3693
3694
3695
3696
3697
3698
3699


5139
5140
5141
5142
5143
5144
5145
5146
5147
5148
5149
5150
5151
5152
5153
5154
5155
5156
5157
5158
5159
5160
5161
5162
5163
5164
5165
5166
5167
5168
5169
5170
5171
5172
5173
5174
5175
5176
5177
5178
5179
5180
5181
5182
5183
5184
5185
5186
5187
5188
5189
5190
5191
5192
5193
5194
5195
5196
5197
5198
5199
5200
5201
5202
5203
5204
5205
5206
5207
5208
5209
5210
5211
5212
5213
5214
5215
5216
5217
5218
5219
5220
5221
5222
5223
5224
5225
5226
5227
5228
5229
5230
5231
5232
5233
5234
5235
5236
5237
5238
5239
5240
5241
5242
5243
5244
5245
5246
5247
5248
5249
5250
5251
5252
5253
5254
5255
5256
5257
5258
5259
5260
5261
5262
5263
5264
5265
5266
5267
5268
5269
5270
5271
5272
5273
5274
5275
5276
5277
5278
5279
5280
5281
5282
5283
5284
5285
5286
5287
5288
5289
5290
5291
5292
5293
5294
5295
5296
5297
5298
5299
5300
5301
5302
5303
5304
5305
5306
5307
5308
5309
5310
5311
5312
5313
5314
5315
5316
5317
5318
5319
5320
5321
5322
5323
5324
5325
5326
5327
5328
5329
5330
5331
5332
5333
5334
5335
5336
5337
5338


8416
8417
8418
8419
8420
8421
8422
8423
8424
8425
8426
8427
8428
8429
8430
8431
8432
8433
8434
8435
8436
8437
8438
8439
8440
8441
8442
8443
8444
8445
8446
8447
8448
8449
8450
8451
8452
8453
8454
8455
8456
8457
8458
8459
8460
8461
8462
8463
8464
8465
8466
8467
8468
8469
8470
8471
8472
8473
8474
8475
8476
8477
8478
8479
8480
8481
8482
8483
8484
8485
8486
8487
8488
8489
8490
8491
8492
8493
8494
8495
8496
8497
8498
8499
8500
8501
8502
8503
8504
8505
8506
8507
8508
8509
8510
8511
8512
8513
8514
8515
8516
8517
8518
8519
8520
8521
8522
8523
8524
8525
8526
8527
8528
8529
8530
8531
8532
8533
8534
8535
8536
8537
8538
8539
8540
8541
8542
8543
8544
8545
8546
8547
8548
8549
8550
8551
8552
8553
8554
8555
8556
8557
8558
8559
8560
8561
8562
8563
8564
8565
8566
8567
8568
8569
8570
8571
8572
8573
8574
8575
8576
8577
8578
8579
8580
8581
8582
8583
8584
8585
8586
8587
8588
8589
8590
8591
8592
8593
8594
8595
8596
8597
8598
8599
8600
8601
8602
8603
8604
8605
8606
8607
8608
8609
8610
8611
8612
8613
8614
8615


10046
10047
10048
10049
10050
10051
10052
10053
10054
10055
10056
10057
10058
10059
10060
10061
10062
10063
10064
10065
10066
10067
10068
10069
10070
10071
10072
10073
10074
10075
10076
10077
10078
10079
10080
10081
10082
10083
10084
10085
10086
10087
10088
10089
10090
10091
10092
10093
10094
10095
10096
10097
10098
10099
10100
10101
10102
10103
10104
10105
10106
10107
10108
10109
10110
10111
10112
10113
10114
10115
10116
10117
10118
10119
10120
10121
10122
10123
10124
10125
10126
10127
10128
10129
10130
10131
10132
10133
10134
10135
10136
10137
10138
10139
10140
10141
10142
10143
10144
10145
10146
10147
10148
10149
10150
10151
10152
10153
10154
10155
10156
10157
10158
10159
10160
10161
10162
10163
10164
10165
10166
10167
10168
10169
10170
10171
10172
10173
10174
10175
10176
10177
10178
10179
10180
10181
10182
10183
10184
10185
10186
10187
10188
10189
10190
10191
10192
10193
10194
10195
10196
10197
10198
10199
10200
10201
10202
10203
10204
10205
10206
10207
10208
10209
10210
10211
1021

11412
11413
11414
11415
11416
11417
11418
11419
11420
11421
11422
11423
11424
11425
11426
11427
11428
11429
11430
11431
11432
11433
11434
11435
11436
11437
11438
11439
11440
11441
11442
11443
11444
11445
11446
11447
11448
11449
11450
11451
11452
11453
11454
11455
11456
11457
11458
11459
11460
11461
11462
11463
11464
11465
11466
11467
11468
11469
11470
11471
11472
11473
11474
11475
11476
11477
11478
11479
11480
11481
11482
11483
11484
11485
11486
11487
11488
11489
11490
11491
11492
11493
11494
11495
11496
11497
11498
11499
11500
11501
11502
11503
11504
11505
11506
11507
11508
11509
11510
11511
11512
11513
11514
11515
11516
11517
11518
11519
11520
11521
11522
11523
11524
11525
11526
11527
11528
11529
11530
11531
11532
11533
11534
11535
11536
11537
11538
11539
11540
11541
11542
11543
11544
11545
11546
11547
11548
11549
11550
11551
11552
11553
11554
11555
11556
11557
11558
11559
11560
11561
11562
11563
11564
11565
11566
11567
11568
11569
11570
11571
11572
11573
11574
11575
11576
11577
1157

12778
12779
12780
12781
12782
12783
12784
12785
12786
12787
12788
12789
12790
12791
12792
12793
12794
12795
12796
12797
12798
12799
12800
12801
12802
12803
12804
12805
12806
12807
12808
12809
12810
12811
12812
12813
12814
12815
12816
12817
12818
12819
12820
12821
12822
12823
12824
12825
12826
12827
12828
12829
12830
12831
12832
12833
12834
12835
12836
12837
12838
12839
12840
12841
12842
12843
12844
12845
12846
12847
12848
12849
12850
12851
12852
12853
12854
12855
12856
12857
12858
12859
12860
12861
12862
12863
12864
12865
12866
12867
12868
12869
12870
12871
12872
12873
12874
12875
12876
12877
12878
12879
12880
12881
12882
12883
12884
12885
12886
12887
12888
12889
12890
12891
12892
12893
12894
12895
12896
12897
12898
12899
12900
12901
12902
12903
12904
12905
12906
12907
12908
12909
12910
12911
12912
12913
12914
12915
12916
12917
12918
12919
12920
12921
12922
12923
12924
12925
12926
12927
12928
12929
12930
12931
12932
12933
12934
12935
12936
12937
12938
12939
12940
12941
12942
12943
1294

14144
14145
14146
14147
14148
14149
14150
14151
14152
14153
14154
14155
14156
14157
14158
14159
14160
14161
14162
14163
14164
14165
14166
14167
14168
14169
14170
14171
14172
14173
14174
14175
14176
14177
14178
14179
14180
14181
14182
14183
14184
14185
14186
14187
14188
14189
14190
14191
14192
14193
14194
14195
14196
14197
14198
14199
14200
14201
14202
14203
14204
14205
14206
14207
14208
14209
14210
14211
14212
14213
14214
14215
14216
14217
14218
14219
14220
14221
14222
14223
14224
14225
14226
14227
14228
14229
14230
14231
14232
14233
14234
14235
14236
14237
14238
14239
14240
14241
14242
14243
14244
14245
14246
14247
14248
14249
14250
14251
14252
14253
14254
14255
14256
14257
14258
14259
14260
14261
14262
14263
14264
14265
14266
14267
14268
14269
14270
14271
14272
14273
14274
14275
14276
14277
14278
14279
14280
14281
14282
14283
14284
14285
14286
14287
14288
14289
14290
14291
14292
14293
14294
14295
14296
14297
14298
14299
14300
14301
14302
14303
14304
14305
14306
14307
14308
14309
1431

15510
15511
15512
15513
15514
15515
15516
15517
15518
15519
15520
15521
15522
15523
15524
15525
15526
15527
15528
15529
15530
15531
15532
15533
15534
15535
15536
15537
15538
15539
15540
15541
15542
15543
15544
15545
15546
15547
15548
15549
15550
15551
15552
15553
15554
15555
15556
15557
15558
15559
15560
15561
15562
15563
15564
15565
15566
15567
15568
15569
15570
15571
15572
15573
15574
15575
15576
15577
15578
15579
15580
15581
15582
15583
15584
15585
15586
15587
15588
15589
15590
15591
15592
15593
15594
15595
15596
15597
15598
15599
15600
15601
15602
15603
15604
15605
15606
15607
15608
15609
15610
15611
15612
15613
15614
15615
15616
15617
15618
15619
15620
15621
15622
15623
15624
15625
15626
15627
15628
15629
15630
15631
15632
15633
15634
15635
15636
15637
15638
15639
15640
15641
15642
15643
15644
15645
15646
15647
15648
15649
15650
15651
15652
15653
15654
15655
15656
15657
15658
15659
15660
15661
15662
15663
15664
15665
15666
15667
15668
15669
15670
15671
15672
15673
15674
15675
1567

In [77]:
df_writers_producers.iloc[0:25,]

writer   producer     tconst parentTconst seasonNumber episodeNumber
0   nm0172830  nm0951642  tt0200656    tt0132666            3            12
1   nm0827670  nm0951642  tt0200656    tt0132666            3            12
2   nm2381451  nm0128325  tt0200809    tt0132666            3             8
3   nm0638586  nm0255782  tt0215111    tt0066684           30             5
4   nm0375285  nm0546161  tt0217557    tt0250157            1             0
5   nm0571113  nm0079542  tt0232002    tt0132666            3             7
6   nm0927618  nm0665494  tt0233274    tt0132666            4            13
7   nm0581224  nm0079542  tt0246786    tt0132666            4             4
8   nm0236494  nm0613774  tt0290529    tt0283205            1             9
9   nm0236494  nm0613774  tt0290569    tt0283205            1             7
10  nm0506087  nm0926151  tt0306666    tt1466074           13             5
11  nm1297877  nm0926151  tt0306666    tt1466074           13             5
12  nm0512894  nm0926151  tt0306666    tt1466074           13             5
13  nm0106563  nm0058454  tt0308593    tt0312172            1             1
14  nm0128874  nm0313394  tt0324030    tt0132666           44            21
15  nm0290900  nm0004475  tt0329200    tt0132666            5            14
16  nm0371235  nm0004475  tt0329200    tt0132666            5            14
17  nm0131969  nm0410504  tt0332663    tt0320038            1             1
18  nm0131969  nm0569461  tt0332663    tt0320038            1             1
19  nm0860513  nm0410504  tt0332663    tt0320038            1             1
20  nm0860513  nm0569461  tt0332663    tt0320038            1             1
21  nm1411800  nm0754978  tt0346932    tt0132666           44            26
22  nm1411800  nm0011851  tt0346932    tt0132666           44            26
23  nm0115114  nm0754978  tt0346932    tt0132666           44            26
24  nm0115114  nm0011851  tt0346932    tt0132666           44            26

In [78]:
df_titles.iloc[0:20,21:40]

writer1    writer2    writer3 writer4 writer5 writer6 writer7 writer8  \
2    nm0172830  nm0827670       None    None    None    None    None    None   
3    nm2381451       None       None    None    None    None    None    None   
5    nm0638586       None       None    None    None    None    None    None   
6    nm0375285       None       None    None    None    None    None    None   
11   nm0571113       None       None    None    None    None    None    None   
13   nm0927618       None       None    None    None    None    None    None   
18   nm0581224       None       None    None    None    None    None    None   
61   nm0236494       None       None    None    None    None    None    None   
62   nm0236494       None       None    None    None    None    None    None   
80   nm0506087  nm1297877  nm0512894    None    None    None    None    None   
81   nm0106563       None       None    None    None    None    None    None   
94   nm0128874       None       None    None    None    None    None    None   
99   nm0290900  nm0371235       None    None    None    None    None    None   
101  nm0131969  nm0860513       None    None    None    None    None    None   
110  nm1411800  nm0115114       None    None    None    None    None    None   
118  nm0471352  nm0511541       None    None    None    None    None    None   
135  nm0006809       None       None    None    None    None    None    None   
137  nm0041469       None       None    None    None    None    None    None   
144  nm0523299       None       None    None    None    None    None    None   
153  nm0645640  nm0275368       None    None    None    None    None    None   

    writer9                                 producers  producer1  producer2  \
2      None                                ,nm0951642  nm0951642       None   
3      None                                ,nm0128325  nm0128325       None   
5      None                                ,nm0255782  nm0255782       None   
6      None                                ,nm0546161  nm0546161       None   
11     None                                ,nm0079542  nm0079542       None   
13     None                                ,nm0665494  nm0665494       None   
18     None                                ,nm0079542  nm0079542       None   
61     None                                ,nm0613774  nm0613774       None   
62     None                                ,nm0613774  nm0613774       None   
80     None                                ,nm0926151  nm0926151       None   
81     None                                ,nm0058454  nm0058454       None   
94     None                                ,nm0313394  nm0313394       None   
99     None                                ,nm0004475  nm0004475       None   
101    None                      ,nm0410504,nm0569461  nm0410504  nm0569461   
110    None                      ,nm0754978,nm0011851  nm0754978  nm0011851   
118    None                                ,nm0321782  nm0321782       None   
135    None  ,nm0906943,nm0184586,nm0746362,nm0833403  nm0906943  nm0184586   
137    None                                ,nm0326177  nm0326177       None   
144    None                      ,nm1106288,nm0851395  nm1106288  nm0851395   
153    None                      ,nm0901880,nm3152781  nm0901880  nm3152781   

     producer3  producer4 producer5 producer6 producer7  
2         None       None      None      None      None  
3         None       None      None      None      None  
5         None       None      None      None      None  
6         None       None      None      None      None  
11        None       None      None      None      None  
13        None       None      None      None      None  
18        None       None      None      None      None  
61        None       None      None      None      None  
62        None       None      None      None      None  
80        None       None      None      None      None  
81        None       None   

In [80]:
# save as file
save_csv(df_writers_producers, 'df_writers_producers1', path=wd)

In [82]:
# number of collaborations: 53,701
len(df_writers_producers.index)

53701

In [83]:
# drop duplicate rows --> multiple cooperations/episodes within one season of the same series are only
# considered as one cooperation

# new column: True if row is duplicated (first occurence is set to False, further occurences are True)
df_writers_producers['duplicated'] = df_writers_producers.duplicated(['writer','producer','parentTconst','seasonNumber'])
df_writers_producers['duplicated'].value_counts()

# drop duplicate rows
df_writers_producers = df_writers_producers[df_writers_producers['duplicated'] == False]

# number of collaborations: 21,221
len(df_writers_producers.index)

21221

In [84]:
# save as file
save_csv(df_writers_producers, 'df_writers_producers2', path=wd)

In [ ]:
# reduce columns of df_writers_producers
df_writers_producers = df_writers_producers[['writer','producer']]

In [85]:
# check if there are individuals who are both writers and producers
writers=set(df_writers_producers.writer.tolist())
producers=set(df_writers_producers.producer.tolist())

writer_producers = list(writers.intersection(producers))

In [86]:
# check for individuals who are both whether they are primilarily writers or producers

counts = []
for i in range(len(writer_producers)):
    indiv = writer_producers[i]
    count_w = df_writers_producers.loc[df_writers_producers.writer == indiv, 'writer'].count()
    count_p = df_writers_producers.loc[df_writers_producers.producer == indiv, 'producer'].count()
    count = [indiv, count_w, count_p]
    counts.append(count)

# sort individuals in lists 
mainly_writers = []
mainly_producers = []
unclear = []

for i in range(len(counts)):
    indiv=counts[i]
    if indiv[1] > indiv[2]:
        mainly_writers.append(indiv[0])
    elif indiv[2] > indiv[1]:
        mainly_producers.append(indiv[0])
    else:
        unclear.append(indiv[0])

In [87]:
# drop cases where individual has job which is not his/her primary job

df_writers_producers['delete'] = 0

# delete cases when mainly writers are producers
for i in range(len(mainly_writers)):
    indiv = mainly_writers[i]
    df_writers_producers.loc[df_writers_producers.producer == indiv, 'delete'] = 1
    
# delete cases when mainly producers are writers
for i in range(len(mainly_producers)):
    indiv = mainly_producers[i]
    df_writers_producers.loc[df_writers_producers.writer == indiv, 'delete'] = 1

# delete unclear cases
for i in range(len(unclear)):
    indiv = unclear[i]
    df_writers_producers.loc[df_writers_producers.writer == indiv, 'delete'] = 1
    df_writers_producers.loc[df_writers_producers.producer == indiv, 'delete'] = 1
       
df_writers_producers = df_writers_producers[df_writers_producers.delete == 0]

In [88]:
# check for cases where individuals are both writer and producer for the same production
double_job = []

for i in df_writers_producers.index:
    w = df_writers_producers.loc[i,'writer']
    p = df_writers_producers.loc[i, 'producer']
    if w == p:
        double_job.append(w)

double_job
# --> None such cases

[]

In [89]:
# save
save_csv(df_writers_producers, 'df_writers_producers3',path=wd)

In [175]:
# number of collaborations: 17,574
len(df_writers_producers.index)

17574

In [174]:
# load data
#df_writers_producers = import_tsv('df_writers_producers3.csv')

In [176]:
# update dataframe to include weights: number of collaborations between one writer-producer pair
df_writers_producers = df_writers_producers.groupby(['writer','producer']).size().to_frame(name='coop').reset_index()

In [180]:
# control
df_writers_producers.iloc[1000:1025]

writer   producer  coop
1000  nm0106563  nm0172670     2
1001  nm0106563  nm0188312     6
1002  nm0106563  nm0275935     1
1003  nm0106563  nm1342242     1
1004  nm0107302  nm0215973     1
1005  nm0107302  nm0264248     1
1006  nm0107302  nm0472477     3
1007  nm0107302  nm0799047     2
1008  nm0107302  nm1558784     4
1009  nm0107302  nm1692438     1
1010  nm0107302  nm2153315     2
1011  nm0107302  nm2212351     1
1012  nm0107302  nm5263944     1
1013  nm0107402  nm0006460     1
1014  nm0107402  nm0069072    10
1015  nm0107402  nm0319666     1
1016  nm0107402  nm0850386     1
1017  nm0107402  nm0876590     9
1018  nm0107402  nm0926252     3
1019  nm0107402  nm1433339     1
1020  nm0107402  nm2266269     2
1021  nm0107774  nm0381868     1
1022  nm0107774  nm0401205     1
1023  nm0107774  nm1241294     1
1024  nm0107774  nm1431798     1

In [181]:
# save
save_csv(df_writers_producers, 'df_writers_producers4',path=wd)

### Add gender information for writers and producers

#### 1st step: extract from Wikidata

In [93]:
# import query return from Wikidata
query_writers = import_csv(wd+'query_writers.csv')
query_producers = import_csv(wd+'query_producers.csv')
query_directors = import_csv(wd+'query_directors.csv')
query_actors_us = import_csv(wd+'query_actors_us.csv')
query_actors_uk = import_csv(wd+'query_actors_uk.csv')

In [94]:
# append datasets to one
query_wd = query_writers.append(query_producers, ignore_index = True)
query_wd = query_wd.append(query_directors, ignore_index = True)
query_wd = query_wd.append(query_actors_us, ignore_index = True)
query_wd = query_wd.append(query_actors_uk, ignore_index = True)

In [95]:
# remove duplicates from query_wd (some are listed under various categories)

# 1) new column: True if row is duplicated (first occurence is set to False, further occurences are True)
query_wd['duplicated'] = query_wd.duplicated(['item','itemLabel'])

# 2) drop duplicate rows
query_wd = query_wd[query_wd['duplicated'] == False]

In [96]:
# save reduced dataset
save_csv(query_wd, 'query_all', path=wd)

In [ ]:
# load df_writers_producers
#df_writers_producers = import_tsv('df_writers_producers4.csv')

In [97]:
# make lists of all writers / producers

writers=list(set(df_writers_producers.writer.tolist()))
producers=list(set(df_writers_producers.producer.tolist()))
writers_and_producers = writers + producers

In [98]:
# load IMDb dataset with info on individuals
df_name_info = import_tsv('name.basics.tsv/data.tsv')

In [99]:
# drop cases in name_info of names not in writers_and_producers list
df_name_info = df_name_info[df_name_info['nconst'].isin(writers_and_producers)]

In [100]:
# save reduced dataset
save_csv(df_name_info, 'df_name_info1', path=wd)

In [101]:
# add column for gender based on Wikidata
df_name_info['gender'] = '-'

In [104]:
# list of all names extracted from wikidata under categories screenwriter, producer, director, actor,...
wd_names = query_wd['itemLabel'].tolist()
wd_names

['Douglas Adams',
 'Elvis Presley',
 'Bob Dylan',
 'Carl Sagan',
 'Bill Maher',
 'Wladimir Semjonowitsch Wyssozki',
 'Dario Fo',
 'Michail Afanassjewitsch Bulgakow',
 'Andrei Arsenjewitsch Tarkowski',
 'Charlie Chaplin',
 'Franz Kafka',
 'Jorge Luis Borges',
 'Harry Mulisch',
 'Leonard Cohen',
 'Leonardo Ortolani',
 'Luigi Pirandello',
 'Françoise Sagan',
 'Jacques Brel',
 'Serge Gainsbourg',
 'Madonna',
 'Charles Aznavour',
 'Stanley Kubrick',
 'Cesare Pavese',
 'David Lynch',
 'Coluche',
 'Tom Hanks',
 'Totò',
 'Mark Millar',
 'Matthew Vaughn',
 'Paul McCartney',
 'Ringo Starr',
 'Chuck Norris',
 'Louis de Funès',
 'Michael Jackson',
 'George Orwell',
 'Quentin Tarantino',
 'Tony Barbieri',
 'Chris Rock',
 'Adam Carolla',
 'Elsa Triolet',
 'James Coburn',
 'Doug Lawrence',
 'Eric Bana',
 'Peter Jackson',
 'Jennette McCurdy',
 'Vince Gilligan',
 'Jonathan Winters',
 'Sean Connery',
 'Barbra Streisand',
 'Paul Otto',
 'Jimmy Kimmel',
 'Jason Lee',
 'Salvador Dalí',
 'Andy Warhol',
 'Ch

In [105]:
# number of names to be checked on Wikidata: 7,231
len(writers_and_producers)

7231

In [108]:
# extract gender info from Wikidata:
# loop over df_name_info, check if name is in Wikidata list, and extract gender from Wikidata if provided
# Warning: loop takes quite a while!

# list for those not found in wikidata
not_in_wikidata = []

# list for those with no gender info in wikidata
no_gender_info = []

# counter to check progression of following loop
counter=0

# loop: insert gender information if available on wikidata
for i in df_name_info.index:
    name=df_name_info.loc[i,'primaryName']
    print(counter, name)
    if name not in wd_names:
        not_in_wikidata.append(name)
        counter=counter+1
        continue
    if name in wd_names:
        q = query_wd.loc[query_wd['itemLabel'] == name, 'item']
        q=q.values[0]
        q=re.sub(r'http://www.wikidata.org/entity/','',q)
        p = wptools.page(wikibase = q).get_wikidata()
        try:
            gender= p.data['claims'].get('P21')[0]
            df_name_info.loc[i, 'gender'] = gender
            counter=counter+1
        except TypeError:
            no_gender_info.append(name)
            counter=counter+1

0 Brad Pitt


www.wikidata.org (wikidata) Q35332
www.wikidata.org (labels) P5587|P7293|Q30|Q3476361|P6150|Q843999|...
www.wikidata.org (labels) Q165192|P7859|P3136|Q65|P2163|P7214|Q70...
www.wikidata.org (labels) Q10798782|Q6404277|P1266|P950|P5019|P72...
www.wikidata.org (labels) P1296|P6521|Q121842|P3995|P3280|P5340|Q...
www.wikidata.org (labels) Q202466|Q6581097|Q106291|P1315|P3933|P2...
en.wikipedia.org (imageinfo) File:Brad Pitt 2019 by Glenn Francis.jpg
Brad Pitt (en) data
{
  aliases: <list(2)> William Bradley Pitt, Brad Jolie-Pitt
  claims: <dict(147)> P19, P26, P106, P166, P373, P214, P213, P434...
  description: American actor and filmmaker
  image: <list(1)> {'file': 'File:Brad Pitt 2019 by Glenn Francis....
  label: Brad Pitt
  labels: <dict(223)> P5587, P7293, Q30, Q3476361, P6150, Q843999,...
  modified: <dict(1)> wikidata
  requests: <list(7)> wikidata, labels, labels, labels, labels, la...
  title: Brad_Pitt
  what: human
  wikibase: Q35332
  wikidata: <dict(147)> place of birth (P19

1 James Cameron


www.wikidata.org (labels) P5587|Q150|P856|P1280|P910|P1670|P551|P...
www.wikidata.org (labels) Q7042855|P2688|P1559|P2638|P1006|P2639|...
www.wikidata.org (labels) P3417|P569|P7902|P7803|Q15278107|P2605|...
www.wikidata.org (labels) P373|P227|P21|P3106|P734|Q6581097|Q16|P...
en.wikipedia.org (imageinfo) File:James Cameron by Gage Skidmore....
James Cameron (en) data
{
  aliases: <list(2)> James Francis Cameron, Jim Cameron
  claims: <dict(123)> P166, P1233, P21, P18, P19, P26, P27, P214, ...
  description: Canadian film director
  image: <list(2)> {'file': 'File:James Cameron by Gage Skidmore.j...
  label: James Cameron
  labels: <dict(172)> P5587, Q150, P856, P1280, P910, P1670, P551,...
  modified: <dict(1)> wikidata
  requests: <list(6)> wikidata, labels, labels, labels, labels, im...
  title: James_Cameron
  what: human
  wikibase: Q42574
  wikidata: <dict(123)> award received (P166), ISFDB author ID (P1...
  wikidata_pageid: 44814
  wikidata_url: https://www.wikidata.org/wiki/Q425

2 Whoopi Goldberg


...

www.wikidata.org (labels) Q2843|P1280|Q64|P866|Q11774202|Q28389|P...
www.wikidata.org (labels) P1375|P7902|P569|Q61|P2605|P1412|Q11703...
en.wikipedia.org (imageinfo) File:Peter Schneider 2008 02.jpg
Peter Schneider (writer) (en) data
{
  claims: <dict(66)> P31, P21, P19, P735, P27, P569, P106, P18, P3...
  description: German writer
  image: <list(1)> {'file': 'File:Peter Schneider 2008 02.jpg', 'k...
  label: Peter Schneider
  labels: <dict(87)> Q2843, P1280, Q64, P866, Q11774202, Q28389, P...
  modified: <dict(1)> wikidata
  requests: <list(4)> wikidata, labels, labels, imageinfo
  title: Peter_Schneider_(writer)
  what: human
  wikibase: Q3900936
  wikidata: <dict(66)> instance of (P31), sex or gender (P21), pla...
  wikidata_pageid: 3722019
  wikidata_url: https://www.wikidata.org/wiki/Q3900936
}
www.wikidata.org (wikidata) Q4717820


7202 Andrea Lee
7203 Kendall Rogers
7204 Valerie Chu
7205 Ryan Enright
7206 Rose McAleese
7207 John Parolski
7208 Christa Troester
7209 Anthony Jariany
7210 Julie Wong
7211 Christy Miller
7212 Biz LaChance
7213 Emma K. Drewry
7214 Johnny Sciortino
7215 Alexandra Lee
7216 Alex Smith


www.wikidata.org (labels) Q13258171|P19|Q5092|Q717897|Q174193|P10...
en.wikipedia.org (imageinfo) File:WillieAndersonAlexSmith.jpg


7217 Jessica Hernandez Wynn
7218 Carlos Rios
7219 Sam Jarvis
7220 Erickka Sy Savane'
7221 George Crews
7222 Leon Freeman Jr.
7223 John McCutcheon
7224 Anna Jordan
7225 Ben Myer
7226 Andre J. Ferguson
7227 Aniz Adam Ansari
7228 Ali Gusberg
7229 Justice Schiappa
7230 Krista Jensen


Alex Smith (golfer) (en) data
{
  aliases: <list(1)> Alexander Smith
  claims: <dict(17)> P21, P570, P31, P646, P569, P106, P735, P734,...
  description: member of a famous Scottish golfing family
  image: <list(1)> {'file': 'File:WillieAndersonAlexSmith.jpg', 'k...
  label: Alex Smith
  labels: <dict(29)> Q13258171, P19, Q5092, Q717897, Q174193, P106...
  modified: <dict(1)> wikidata
  requests: <list(3)> wikidata, labels, imageinfo
  title: Alex_Smith_(golfer)
  what: human
  wikibase: Q4717820
  wikidata: <dict(17)> sex or gender (P21), date of death (P570), ...
  wikidata_pageid: 4508250
  wikidata_url: https://www.wikidata.org/wiki/Q4717820
}


In [109]:
# save updated dataset
save_csv(df_name_info, 'df_name_info2', path=wd)

# save 'not in wikidata' list
with open(wd+'no_wikidata.txt', 'w') as filehandle:
    for name in not_in_wikidata:
        filehandle.write('%s\n' % name)

In [182]:
df_name_info = import_tsv(wd+'df_name_info2.csv')

In [183]:
# convert gender codes from wikidata to male, female, etc.
     
for i in df_name_info.index:
    name=df_name_info.loc[i,'primaryName']
    if name in wd_names:
        gender=df_name_info.loc[i,'gender']
        if gender == 'Q6581097':
            df_name_info.loc[i,'gender'] = 'male'
            continue
        if gender == 'Q6581072':
            df_name_info.loc[i,'gender'] = 'female'
            continue
        if gender == 'Q1097630':
            df_name_info.loc[i,'gender'] = 'intersexual'
            continue
        if gender == 'Q1052281':
            df_name_info.loc[i,'gender'] = 'trans woman'
            continue
        if gender == 'Q2449503':
            df_name_info.loc[i,'gender'] = 'trans man'
            continue
        if gender == 'Q48270':
             df_name_info.loc[i,'gender'] = 'non binary'


In [184]:
# save updated dataset
save_csv(df_name_info, 'df_name_info3', path=wd)

In [185]:
# how many have been categorized?
df_name_info['gender'].value_counts()

# 5,044 uncategorized
# 1,603 male, 579 female, 4 trans woman, 1 non binary

-              5044
male           1603
female          579
trans woman       4
non binary        1
Name: gender, dtype: int64

#### 2nd step: set to female if profession includes 'actress'

In [186]:
for i in df_name_info.index:
    if df_name_info.loc[i,'gender'] == '-':
        profession = df_name_info.loc[i,'primaryProfession']
        profession = str(profession)
        if 'actress' in profession:
            df_name_info.loc[i,'gender'] = 'female'

In [187]:
# how many have been categorized?
df_name_info['gender'].value_counts()

# 4,748 uncategorized
# 875 female, ...

-              4748
male           1603
female          875
trans woman       4
non binary        1
Name: gender, dtype: int64

#### 3rd step: guess name based on first name

In [188]:
# extract first name
df_name_info['first_name'] = '-'

for i in df_name_info.index:
    name = df_name_info.loc[i,'primaryName']
    firstname = name.split()[0]
    df_name_info.loc[i,'first_name'] = firstname

In [189]:
# use module gender-guesser: guesses gender based on first name

df_name_info['gender_guessed'] = '-'

d = gender_guesser.detector.Detector()

for i in df_name_info.index:
    name = df_name_info.loc[i,'first_name']
    guess=d.get_gender(name)
    df_name_info.loc[i,'gender_guessed'] = guess

In [190]:
# save
save_csv(df_name_info, 'df_name_info4', path=wd)

In [191]:
# combine columns 'gender' and 'gender_guessed' to column 'gender_combined'

df_name_info['gender_combined'] = '-'

for i in df_name_info.index:
    if df_name_info.loc[i,'gender'] != '-':
        df_name_info.loc[i,'gender_combined'] = df_name_info.loc[i,'gender']
    if df_name_info.loc[i,'gender'] == '-':
        if df_name_info.loc[i,'gender_guessed'] == 'female' or df_name_info.loc[i,'gender_guessed'] == 'male':
            df_name_info.loc[i,'gender_combined'] = df_name_info.loc[i,'gender_guessed']

In [192]:
# How many categorized?
df_name_info['gender_combined'].value_counts()

# male: 4,267, female: 2,155, ...
# uncategorized: 804

male           4267
female         2155
-               804
trans woman       4
non binary        1
Name: gender_combined, dtype: int64

In [193]:
# categorize as male if gender guesser says 'mostly male' and profession includes 'actor'
for i in df_name_info.index:
    if df_name_info.loc[i,'gender_combined'] == '-':
        if 'actor' in df_name_info.loc[i,'primaryProfession'] and df_name_info.loc[i,'gender_guessed'] == 'mostly_male':
            df_name_info.loc[i,'gender_combined'] = 'male'
            
df_name_info['gender_combined'].value_counts()

# male: 4,302, ...
# uncategorized: 769

male           4302
female         2155
-               769
trans woman       4
non binary        1
Name: gender_combined, dtype: int64

In [194]:
save_csv(df_name_info, 'df_name_info5', path=wd)

#### 4th step: handcode remaining cases if possible

In [195]:
# list of unclassified
unclassified = []
for i in df_name_info.index:
    if df_name_info.loc[i,'gender_combined'] == '-':
        unclassified.append(df_name_info.loc[i,'primaryName'])     
    
# save as txt
with open('D:/IMDb Daten/unclassified.txt', 'w') as filehandle:
    for name in unclassified:
        filehandle.write('%s\n' % name)

Handcoding:
- ...
- ...
- ...

In [196]:
# load handcoded data
df_classifiedCSV = wd+'classified.csv'
df_classified = pd.read_csv(df_classifiedCSV, sep=';',encoding='utf-8')

In [197]:
# match hand coded data to dataset df_name_info
for i in df_name_info.index:
    if df_name_info.loc[i,'gender_combined'] == '-':
        name=df_name_info.loc[i,'primaryName']
        gender = df_classified.loc[df_classified['primaryName'] == name, 'gender']
        gender= gender.iat[0]
        if gender != '-':
            df_name_info.loc[i,'gender_combined'] = gender

In [198]:
# How many have been categorized?
df_name_info['gender_combined'].value_counts()

# male_ 4,656, female: 2,484, trans woman: 4, non binary: 3, queer/trans: 1
# uncategorized: 83

male           4656
female         2484
-                83
trans woman       4
non binary        3
queer/trans       1
Name: gender_combined, dtype: int64

In [199]:
save_csv(df_name_info, 'df_name_info6', path=wd)

###  Drop cases from data where gender could not be determined

In [200]:
# list of those who could not be categorized
uncategorized=[]
for i in df_name_info.index:
    if df_name_info.loc[i,'gender_combined'] == '-':
        uncategorized.append(df_name_info.loc[i,'nconst'])

In [ ]:
# load df_writers_producers
#df_writers_producers = import_tsv('df_writers_producers4.csv')

In [201]:
# drop those where gender could not be categorized
df_writers_producers['genderUncategorized_w'] = df_writers_producers['writer'].isin(uncategorized)
df_writers_producers['genderUncategorized_p'] = df_writers_producers['producer'].isin(uncategorized)

df_writers_producers = df_writers_producers[df_writers_producers.genderUncategorized_w == False]
df_writers_producers = df_writers_producers[df_writers_producers.genderUncategorized_p == False]

In [202]:
# number of collaboration pairs: 13,329
len(df_writers_producers.index)

13329

In [203]:
# save
save_csv(df_writers_producers, 'df_writers_producers5',path=wd)

In [204]:
# reduce name_info dataset
# put non binary, trans, etc into one category
# rename variables

df_name_info = df_name_info[df_name_info.gender_combined != '-']

df_name_info['gender_final'] = df_name_info['gender_combined']
df_name_info['gender_final'] = df_name_info['gender_final'].replace(['trans woman','queer/trans','non binary'],'other')
df_name_info = df_name_info.rename(columns={'gender': 'gender_wd', 'gender_final': 'gender'})

In [205]:
# save
save_csv(df_name_info, 'df_name_info7',path=wd)

### Add gender info to df_writers_producers

In [206]:
# add variables 'gender_writer' and 'gender_producer' to writer_producer dataset

females=[]
males=[]
other=[]

for i in df_name_info.index:
    if df_name_info.loc[i,'gender'] == 'male':
        males.append(df_name_info.loc[i,'nconst'])
        continue
    if df_name_info.loc[i,'gender'] == 'female':
        females.append(df_name_info.loc[i,'nconst'])
        continue
    if df_name_info.loc[i,'gender'] == 'other':
        other.append(df_name_info.loc[i,'nconst'])

df_writers_producers['gender_writer'] = ''
df_writers_producers['gender_producer'] = ''
        
for i in df_writers_producers.index:
    writer=df_writers_producers.loc[i,'writer']
    producer=df_writers_producers.loc[i,'producer']
    if writer in males:
        df_writers_producers.loc[i,'gender_writer'] = 'male'
    elif writer in females:
        df_writers_producers.loc[i,'gender_writer'] = 'female'
    elif writer in other:
        df_writers_producers.loc[i,'gender_writer'] = 'other'
    if producer in males:
        df_writers_producers.loc[i,'gender_producer'] = 'male'
    elif producer in females:
        df_writers_producers.loc[i,'gender_producer'] = 'female'
    elif producer in other:
        df_writers_producers.loc[i,'gender_producer'] = 'other'

In [207]:
# save
save_csv(df_writers_producers, 'df_writers_producers6', path=wd)